# [COM6513] Assignment: Topic Classification with a Feedforward Network


### Instructor: Nikos Aletras


The goal of this assignment is to develop a Feedforward neural network for topic classification. 



For that purpose, you will implement:

- Text processing methods for transforming raw text data into input vectors for your network  (**1 mark**)


- A Feedforward network consisting of:
    - **One-hot** input layer mapping words into an **Embedding weight matrix** (**1 mark**)
    - **One hidden layer** computing the mean embedding vector of all words in input followed by a **ReLU activation function** (**1 mark**)
    - **Output layer** with a **softmax** activation. (**1 mark**)


- The Stochastic Gradient Descent (SGD) algorithm with **back-propagation** to learn the weights of your Neural network. Your algorithm should:
    - Use (and minimise) the **Categorical Cross-entropy loss** function (**1 mark**)
    - Perform a **Forward pass** to compute intermediate outputs (**2 marks**)
    - Perform a **Backward pass** to compute gradients and update all sets of weights (**3 marks**)
    - Implement and use **Dropout** after each hidden layer for regularisation (**1 marks**)



- Discuss how did you choose hyperparameters? You can tune the learning rate (hint: choose small values), embedding size {e.g. 50, 300, 500} and the dropout rate {e.g. 0.2, 0.5}. Please use tables or graphs to show training and validation performance for each hyperparameter combination  (**2 marks**). 



- After training a model, plot the learning process (i.e. training and validation loss in each epoch) using a line plot and report accuracy. Does your model overfit, underfit or is about right? (**1 mark**).



- Re-train your network by using pre-trained embeddings ([GloVe](https://nlp.stanford.edu/projects/glove/)) trained on large corpora. Instead of randomly initialising the embedding weights matrix, you should initialise it with the pre-trained weights. During training, you should not update them (i.e. weight freezing) and backprop should stop before computing gradients for updating embedding weights. Report results by performing hyperparameter tuning and plotting the learning process. Do you get better performance? (**1 marks**).



- Extend you Feedforward network by adding more hidden layers (e.g. one more or two). How does it affect the performance? Note: You need to repeat hyperparameter tuning, but the number of combinations grows exponentially. Therefore, you need to choose a subset of all possible combinations (**3 marks**)


- Provide well documented and commented code describing all of your choices. In general, you are free to make decisions about text processing (e.g. punctuation, numbers, vocabulary size) and hyperparameter values. We expect to see justifications and discussion for all of your choices. You must provide detailed explanations of your implementation, provide a detailed analysis of the results (e.g. why a model performs better than other models etc.) including error analyses (e.g. examples and discussion/analysis of missclasifications etc.)  (**10 marks**). 



- Provide efficient solutions by using Numpy arrays when possible. Executing the whole notebook with your code should not take more than 10 minutes on any standard computer (e.g. Intel Core i5 CPU, 8 or 16GB RAM) excluding hyperparameter tuning runs and loading the pretrained vectors. You can find tips in Lab 1 (**2 marks**). 



### Data 

The data you will use for the task is a subset of the [AG News Corpus](http://groups.di.unipi.it/~gulli/AG_corpus_of_news_articles.html) and you can find it in the `./data_topic` folder in CSV format:

- `data_topic/train.csv`: contains 2,400 news articles, 800 for each class to be used for training.
- `data_topic/dev.csv`: contains 150 news articles, 50 for each class to be used for hyperparameter selection and monitoring the training process.
- `data_topic/test.csv`: contains 900 news articles, 300 for each class to be used for testing.

Class 1: Politics, Class 2: Sports, Class 3: Economy

### Pre-trained Embeddings

You can download pre-trained GloVe embeddings trained on Common Crawl (840B tokens, 2.2M vocab, cased, 300d vectors, 2.03 GB download) from [here](http://nlp.stanford.edu/data/glove.840B.300d.zip). No need to unzip, the file is large.

### Save Memory

To save RAM, when you finish each experiment you can delete the weights of your network using `del W` followed by Python's garbage collector `gc.collect()`




### Submission Instructions

You **must** submit a Jupyter Notebook file (assignment_yourusername.ipynb) and an exported PDF version (you can do it from Jupyter: `File->Download as->PDF via Latex`, you need to have a Latex distribution installed e.g. MikTex or MacTex and pandoc). If you are unable to export the pdf via Latex, you can print the notebook web page to a pdf file from your browser (e.g. on Firefox: File->Print->Save to PDF).


You are advised to follow the code structure given in this notebook by completing all given funtions. You can also write any auxilliary/helper functions (and arguments for the functions) that you might need but note that you can provide a full solution without any such functions. Similarly, you can just use only the packages imported below but you are free to use any functionality from the [Python Standard Library](https://docs.python.org/3/library/index.html), NumPy, SciPy (excluding built-in softmax funtcions) and Pandas. You are **not allowed to use any third-party library** such as Scikit-learn (apart from metric functions already provided), NLTK, Spacy, Keras, Pytorch etc.. You should mention if you've used Windows to write and test your code because we mostly use Unix based machines for marking (e.g. Ubuntu, MacOS). 

There is no single correct answer on what your accuracy should be, but correct implementations usually achieve F1-scores around 80\% or higher. The quality of the analysis of the results and discussion is as important as the implementation and accuracy of your models. Please be brief and consice in your discussion and analyses. 

This assignment will be marked out of 30. It is worth 30\% of your final grade in the module.

The deadline for this assignment is **23:59 on Mon, 26 Apr 2023** and it needs to be submitted via Blackboard. Standard departmental penalties for lateness will be applied. We use a range of strategies to **detect [unfair means](https://www.sheffield.ac.uk/ssid/unfair-means/index)**, including Turnitin which helps detect plagiarism. Use of unfair means would result in getting a failing grade.



In [5]:
import pandas as pd
import numpy as np
from collections import Counter
import re
import matplotlib.pyplot as plt
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import random
from time import localtime, strftime
from scipy.stats import spearmanr,pearsonr
import zipfile
import gc
import nltk
# fixing random seed for reproducibility
random.seed(123)
np.random.seed(123)


## Transform Raw texts into training and development data

First, you need to load the training, development and test sets from their corresponding CSV files (tip: you can use Pandas dataframes).

In [ ]:

def read(path):

    f = open(path,'r',encoding='utf-8') #mac不用这行，直接pd.read_csv(path)
    data = pd.read_csv(f).iloc[:,1].values
    return data
def read_label(path):

    f = open(path,'r',encoding='utf-8') #mac不用这行，直接pd.read_csv(path)
    data = pd.read_csv(f).iloc[:,0].values
    return data


train_df = read(path = './data_topic/train.csv') #read value
test_df = read(path = './data_topic/test.csv')
dev_df = read('./data_topic/dev.csv')

train_label = read_label(path = './data_topic/train.csv') #read label
test_label = read_label(path = './data_topic/test.csv')
dev_label = read_label('./data_topic/dev.csv')

In [ ]:
print(train_df)




['Reuters - South Korean police used water cannon in\\central Seoul Sunday to disperse at least 7,000 protesters\\urging the government to reverse a controversial decision to\\send more troops to Iraq.'
 "Reuters - Thousands of Palestinian\\prisoners in Israeli jails began a hunger strike for better\\conditions Sunday, but Israel's security minister said he\\didn't care if they starved to death."
 'AFP - Sporadic gunfire and shelling took place overnight in the disputed Georgian region of South Ossetia in violation of a fragile ceasefire, wounding seven Georgian servicemen.'
 ...
 ' SAN FRANCISCO (Reuters) - Google Inc. &lt;A HREF="http://www.investor.reuters.com/FullQuote.aspx?ticker=GOOG.OQ target=/stocks/quickinfo/fullquote"&gt;GOOG.OQ&lt;/A&gt;., the  world\'s largest search engine, said on Wednesday it sold 19.6  million shares at \\$85 apiece in its long-awaited initial public  offering, raising \\$1.67 billion for the company.'
 'BHP Billiton, the world #39;s biggest mining comp

# Create input representations


To train your Feedforward network, you first need to obtain input representations given a vocabulary. One-hot encoding requires large memory capacity. Therefore, we will instead represent documents as lists of vocabulary indices (each word corresponds to a vocabulary index). 


## Text Pre-Processing Pipeline

To obtain a vocabulary of words. You should: 
- tokenise all texts into a list of unigrams (tip: you can re-use the functions from Assignment 1) 
- remove stop words (using the one provided or one of your preference) 
- remove unigrams appearing in less than K documents
- use the remaining to create a vocabulary of the top-N most frequent unigrams in the entire corpus.


In [ ]:
stop_words = ['a','in','on','at','and','or', 
              'to', 'the', 'of', 'an', 'by', 
              'as', 'is', 'was', 'were', 'been', 'be', 
            'are','for', 'this', 'that', 'these', 'those', 'you', 'i', 'if',
             'it', 'he', 'she', 'we', 'they', 'will', 'have', 'has',
              'do', 'did', 'can', 'could', 'who', 'which', 'what',
              'but', 'not', 'there', 'no', 'does', 'not', 'so', 've', 'their',
             'his', 'her', 'they', 'them', 'from', 'with', 'its']


### Unigram extraction from a document

You first need to implement the `extract_ngrams` function. It takes as input:
- `x_raw`: a string corresponding to the raw text of a document
- `ngram_range`: a tuple of two integers denoting the type of ngrams you want to extract, e.g. (1,2) denotes extracting unigrams and bigrams.
- `token_pattern`: a string to be used within a regular expression to extract all tokens. Note that data is already tokenised so you could opt for a simple white space tokenisation.
- `stop_words`: a list of stop words
- `vocab`: a given vocabulary. It should be used to extract specific features.

and returns:

- a list of all extracted features.


In [ ]:
def extract_ngrams(x_raw, ngram_range=(1,2), token_pattern=r'\b[A-Za-z][A-Za-z]+\b', 
                   stop_words=[], vocab=set()):
    clf = []
    ngram_low = ngram_range[0]
    ngram_high = ngram_range[1]
    sent = re.findall(token_pattern, x_raw.lower()) # lowercase, remove punctuation & non-alphanumeric characters 
    for i, word in enumerate(sent):  # remove stoplist word 
        if word not in stop_words:
            clf.append(word)
    #print("the result is:{}".format（clf）)
    unigram = []
    bigrams = []
    x = [unigram,bigrams]
    
    for i,word in enumerate(clf):
        
        unigram.append(clf[i])
    # print('unigram:{}'.format(unigram))

    for i in range(len(clf)):
        
        bigrams.append(' '.join(clf[i:i+ngram_high]))
        i+=2
    return x
# result = extract_ngrams(x_raw = train_df, stop_words = stop_words)
# print(result)

### Create a vocabulary of n-grams

Then the `get_vocab` function will be used to (1) create a vocabulary of ngrams; (2) count the document frequencies of ngrams; (3) their raw frequency. It takes as input:
- `X_raw`: a list of strings each corresponding to the raw text of a document
- `ngram_range`: a tuple of two integers denoting the type of ngrams you want to extract, e.g. (1,2) denotes extracting unigrams and bigrams.
- `token_pattern`: a string to be used within a regular expression to extract all tokens. Note that data is already tokenised so you could opt for a simple white space tokenisation.
- `stop_words`: a list of stop words
- `min_df`: keep ngrams with a minimum document frequency.
- `keep_topN`: keep top-N more frequent ngrams.

and returns:

- `vocab`: a set of the n-grams that will be used as features.
- `df`: a Counter (or dict) that contains ngrams as keys and their corresponding document frequency as values.
- `ngram_counts`: counts of each ngram in vocab


In [ ]:
def get_vocab(X_raw, ngram_range=(1,2), token_pattern=r'\b[A-Za-z][A-Za-z]+\b', 
              min_df=0, keep_topN=0, 
              stop_words=[]):
    voc_uni = []
    voc_bi = []
    df = {}
    count_uni=0
    count_bi=0
    vocab = [voc_uni,voc_bi]
    for i,sent in enumerate(X_raw): #cycle to get each sentence 
        extract_ngram = extract_ngrams(sent,stop_words=stop_words)
        voc_uni.append(extract_ngram[0])#get unigram list
        voc_bi.append(extract_ngram[1]) #get bigrams list
        set_sent = set(sent)
    ngram_counts = {}
    for word in voc_uni:
        for words in word:
            if words in ngram_counts:
                ngram_counts[words]+=1
            else:
                ngram_counts[words]=0  
            for word_ in set_sent: #calculate document frequency 
                if words in df:
                    df[words]+=1
                else:
                    df[words]=1
                    
    for word in voc_bi:#use dictionary to collect the ngram and corresponding frequency  
        for words in word:
            if words in ngram_counts:
                ngram_counts[words]+=1
            else:
                ngram_counts[words]=0 
            for word_ in set_sent: #calculate document frequency 
                if words in df:
                    df[words]+=1
                else:
                    df[words]=1   
    for words in df: #set min_df to filter the value
        if df[words]<min_df:
            del df[words]
    if keep_topN!=0: #set keep_topN to filter the most N frequent words
        ngram_counts_top = sorted(ngram_counts.items(),key = lambda item:item[1],reverse=True)
        ngram_counts = []
        # print(ngram_counts_top[0])
        for i in range(keep_topN):
            ngram_counts.append(ngram_counts_top[i])
    return vocab, df, ngram_counts
# h,g,k= get_vocab(train_df)
# print(h,g,k)

Now you should use `get_vocab` to create your vocabulary and get document and raw frequencies of unigrams:

In [ ]:
corpus_list = np.concatenate((train_df,test_df,dev_df))
vocab_list,df,ngram_counts=get_vocab(corpus_list,stop_words = stop_words)
vocab_all = []
for words in vocab_list[0]:
    vocab_all.append(words)
for words in vocab_list[1]:
    vocab_all.append(words)
vocab_all = sum(vocab_all,[])
print(vocab_all)

['reuters', 'south', 'korean', 'police', 'used', 'water', 'cannon', 'central', 'seoul', 'sunday', 'disperse', 'least', 'protesters', 'urging', 'government', 'reverse', 'controversial', 'decision', 'send', 'more', 'troops', 'iraq', 'reuters', 'thousands', 'palestinian', 'prisoners', 'israeli', 'jails', 'began', 'hunger', 'strike', 'better', 'conditions', 'sunday', 'israel', 'security', 'minister', 'said', 'didn', 'care', 'starved', 'death', 'afp', 'sporadic', 'gunfire', 'shelling', 'took', 'place', 'overnight', 'disputed', 'georgian', 'region', 'south', 'ossetia', 'violation', 'fragile', 'ceasefire', 'wounding', 'seven', 'georgian', 'servicemen', 'ap', 'dozens', 'rwandan', 'soldiers', 'flew', 'into', 'sudan', 'troubled', 'darfur', 'region', 'sunday', 'first', 'foreign', 'armed', 'force', 'deployed', 'area', 'since', 'arab', 'militiamen', 'began', 'rampage', 'against', 'black', 'african', 'farmers', 'killing', 'thousands', 'reuters', 'rwandan', 'troops', 'airlifted', 'sunday', 'sudan', '

Then, you need to create vocabulary id -> word and word -> vocabulary id dictionaries for reference:

In [ ]:
vocab_id = {}
id_vocab = {}
for i in range(len(vocab_all)):
    vocab_id[i] = vocab_all[i]
for j in range(len(vocab_all)):
    id_vocab[vocab_all[i]]= j
print(vocab_id)


{0: 'reuters', 1: 'south', 2: 'korean', 3: 'police', 4: 'used', 5: 'water', 6: 'cannon', 7: 'central', 8: 'seoul', 9: 'sunday', 10: 'disperse', 11: 'least', 12: 'protesters', 13: 'urging', 14: 'government', 15: 'reverse', 16: 'controversial', 17: 'decision', 18: 'send', 19: 'more', 20: 'troops', 21: 'iraq', 22: 'reuters', 23: 'thousands', 24: 'palestinian', 25: 'prisoners', 26: 'israeli', 27: 'jails', 28: 'began', 29: 'hunger', 30: 'strike', 31: 'better', 32: 'conditions', 33: 'sunday', 34: 'israel', 35: 'security', 36: 'minister', 37: 'said', 38: 'didn', 39: 'care', 40: 'starved', 41: 'death', 42: 'afp', 43: 'sporadic', 44: 'gunfire', 45: 'shelling', 46: 'took', 47: 'place', 48: 'overnight', 49: 'disputed', 50: 'georgian', 51: 'region', 52: 'south', 53: 'ossetia', 54: 'violation', 55: 'fragile', 56: 'ceasefire', 57: 'wounding', 58: 'seven', 59: 'georgian', 60: 'servicemen', 61: 'ap', 62: 'dozens', 63: 'rwandan', 64: 'soldiers', 65: 'flew', 66: 'into', 67: 'sudan', 68: 'troubled', 69: 

### Convert the list of unigrams  into a list of vocabulary indices

Storing actual one-hot vectors into memory for all words in the entire data set is prohibitive. Instead, we will store word indices in the vocabulary and look-up the weight matrix. This is equivalent of doing a dot product between an one-hot vector and the weight matrix. 

First, represent documents in train, dev and test sets as lists of words in the vocabulary:

In [ ]:
def get_eachword(X,ngram_range=(1,2), token_pattern=r'\b[A-Za-z][A-Za-z]+\b', 
                   stop_words=stop_words, vocab=set()):
    X_list = []
    for sent in X:
        each_word = extract_ngrams(sent, ngram_range=(1,2), token_pattern=r'\b[A-Za-z][A-Za-z]+\b', 
                   stop_words=[], vocab=set())
        each_uni_word = each_word[0]
        for word in each_uni_word:
            X_list.append(word)
    return X_list

        

In [ ]:
lX_train = get_eachword(train_df)
X_dev = get_eachword(dev_df)
X_test = get_eachword(test_df)
print(lX_train)

Then convert them into lists of indices in the vocabulary:

[['Reuters - South Korean police used water cannon in\\central Seoul Sunday to disperse at least 7,000 protesters\\urging the government to reverse a controversial decision to\\send more troops to Iraq.'], ["Reuters - Thousands of Palestinian\\prisoners in Israeli jails began a hunger strike for better\\conditions Sunday, but Israel's security minister said he\\didn't care if they starved to death."], ['AFP - Sporadic gunfire and shelling took place overnight in the disputed Georgian region of South Ossetia in violation of a fragile ceasefire, wounding seven Georgian servicemen.'], ["AP - Dozens of Rwandan soldiers flew into Sudan's troubled Darfur region Sunday, the first foreign armed force deployed in the area since Arab militiamen began a rampage against black African farmers, killing thousands."], ["Reuters - Rwandan troops were airlifted on Sunday\\to Sudan's Darfur as the first foreign force there, mandated to\\protect observers monitoring a cease-fire between the Sudanese\\gove

Put the labels `Y` for train, dev and test sets into arrays: 

In [ ]:
Y_train =[]
Y_test=[]
Y_dev= []
for index in train_label:
    Y_train.append([index])
for index in dev_label:
    Y_dev.append([index])
for index in test_label:
    Y_test.append([index])

# db_train = X_train +Y_train
# print(db_train)

[['Reuters - South Korean police used water cannon in\\central Seoul Sunday to disperse at least 7,000 protesters\\urging the government to reverse a controversial decision to\\send more troops to Iraq.'], ["Reuters - Thousands of Palestinian\\prisoners in Israeli jails began a hunger strike for better\\conditions Sunday, but Israel's security minister said he\\didn't care if they starved to death."], ['AFP - Sporadic gunfire and shelling took place overnight in the disputed Georgian region of South Ossetia in violation of a fragile ceasefire, wounding seven Georgian servicemen.'], ["AP - Dozens of Rwandan soldiers flew into Sudan's troubled Darfur region Sunday, the first foreign armed force deployed in the area since Arab militiamen began a rampage against black African farmers, killing thousands."], ["Reuters - Rwandan troops were airlifted on Sunday\\to Sudan's Darfur as the first foreign force there, mandated to\\protect observers monitoring a cease-fire between the Sudanese\\gove

# Network Architecture

Your network should pass each word index into its corresponding embedding by looking-up on the embedding matrix and then compute the first hidden layer $\mathbf{h}_1$:

$$\mathbf{h}_1 = \frac{1}{|x|}\sum_i W^e_i, i \in x$$

where $|x|$ is the number of words in the document and $W^e$ is an embedding matrix $|V|\times d$, $|V|$ is the size of the vocabulary and $d$ the embedding size.

Then $\mathbf{h}_1$ should be passed through a ReLU activation function:

$$\mathbf{a}_1 = relu(\mathbf{h}_1)$$

Finally the hidden layer is passed to the output layer:


$$\mathbf{y} = \text{softmax}(\mathbf{a}_1W) $$ 
where $W$ is a matrix $d \times |{\cal Y}|$, $|{\cal Y}|$ is the number of classes.

During training, $\mathbf{a}_1$ should be multiplied with a dropout mask vector (elementwise) for regularisation before it is passed to the output layer.

You can extend to a deeper architecture by passing a hidden layer to another one:

$$\mathbf{h_i} = \mathbf{a}_{i-1}W_i $$

$$\mathbf{a_i} = relu(\mathbf{h_i}) $$



# Network Training

First we need to define the parameters of our network by initiliasing the weight matrices. For that purpose, you should implement the `network_weights` function that takes as input:

- `vocab_size`: the size of the vocabulary
- `embedding_dim`: the size of the word embeddings
- `hidden_dim`: a list of the sizes of any subsequent hidden layers. Empty if there are no hidden layers between the average embedding and the output layer 
- `num_classes`: the number of the classes for the output layer

and returns:

- `W`: a dictionary mapping from layer index (e.g. 0 for the embedding matrix) to the corresponding weight matrix initialised with small random numbers (hint: use numpy.random.uniform with from -0.1 to 0.1)

Make sure that the dimensionality of each weight matrix is compatible with the previous and next weight matrix, otherwise you won't be able to perform forward and backward passes. Consider also using np.float32 precision to save memory.

In [21]:
def network_weights(vocab_size=1000, embedding_dim=300, 
                    hidden_dim=[], num_classes=3, init_val = 0.5):
    #creat m*n matrix
    # W = np.zeros((vocab_size,embedding_dim))
    hid_dim = hidden_dim[0]
    W_in=np.random.uniform(-0.1,0.1,(vocab_size,embedding_dim))
    W_hid = np.random.uniform(-0.1,0.1,(embedding_dim,hid_dim))
    W_out = np.random.uniform(-0.1,0.1,(hid_dim,num_classes))
    W = (W_in,W_hid,W_out)
    return W
    

In [22]:
W = network_weights(vocab_size=3,embedding_dim=4,hidden_dim=[2], num_classes=2)
print(W)

(array([[-0.06977451, -0.02022474, -0.05182882, -0.0313088 ],
       [ 0.00262563,  0.03332491, -0.0788183 , -0.07382101],
       [-0.03560388,  0.03231287,  0.06930125,  0.01065147]]), array([[ 0.0708905 , -0.02303244],
       [-0.03664242, -0.02914706],
       [-0.06578363,  0.06582253],
       [-0.03226583,  0.01047402]]), array([[ 0.01571029,  0.00430661],
       [-0.09946239,  0.09766908]]))


Then you need to develop a `softmax` function (same as in Assignment 1) to be used in the output layer. 

It takes as input `z` (array of real numbers) and returns `sig` (the softmax of `z`)



In [ ]:
def softmax(z):
    sig = 1/(1+np.exp(-z))
    
    return sig


Now you need to implement the categorical cross entropy loss by slightly modifying the function from Assignment 1 to depend only on the true label `y` and the class probabilities vector `y_preds`:


In [ ]:
def categorical_loss(y, y_preds):
    l = 0
    for i in range(len(y)):
        loss = y[i]* np.log(y_preds)
        l+=loss
        i+=1
    l = l/i
    return l

Then, implement the `relu` function to introduce non-linearity after each hidden layer of your network 
(during the forward pass): 

$$relu(z_i)= max(z_i,0)$$

and the `relu_derivative` function to compute its derivative (used in the backward pass):

  
  relu_derivative($z_i$)=0, if $z_i$<=0, 1 otherwise.
  


Note that both functions take as input a vector $z$ 

Hint use .copy() to avoid in place changes in array z

In [ ]:
def relu(z):
    z_ = z.copy()
    a= np.maximum(0,z_)
    return a
    
def relu_derivative(z):
    dz = []
    for i in range(len(z)):
        if z[i]<=0:
            term = 0
        else:
            term = 1
        dz.appendd(term)
    return dz

During training you should also apply a dropout mask element-wise after the activation function (i.e. vector of ones with a random percentage set to zero). The `dropout_mask` function takes as input:

- `size`: the size of the vector that we want to apply dropout
- `dropout_rate`: the percentage of elements that will be randomly set to zeros

and returns:

- `dropout_vec`: a vector with binary values (0 or 1)

In [ ]:
def dropout_mask(size, dropout_rate):
    dropout_vec = np.ones(size)
    drop_num = int(size * dropout_rate)
    # print(drop_num)
    for i in range(drop_num-1):
        rand = random.randint(0,size-1)
        dropout_vec[rand] = 0
    return dropout_vec
    

In [ ]:
print(dropout_mask(10, 0.2))
print(dropout_mask(10, 0.2))
# random.randint(1,4)

[0. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
[1. 1. 1. 1. 0. 1. 1. 1. 1. 1.]


Now you need to implement the `forward_pass` function that passes the input x through the network up to the output layer for computing the probability for each class using the weight matrices in `W`. The ReLU activation function should be applied on each hidden layer. 

- `x`: a list of vocabulary indices each corresponding to a word in the document (input)
- `W`: a list of weight matrices connecting each part of the network, e.g. for a network with a hidden and an output layer: W[0] is the weight matrix that connects the input to the first hidden layer, W[1] is the weight matrix that connects the hidden layer to the output layer.
- `dropout_rate`: the dropout rate that is used to generate a random dropout mask vector applied after each hidden layer for regularisation.

and returns:

- `out_vals`: a dictionary of output values from each layer: h (the vector before the activation function), a (the resulting vector after passing h from the activation function), its dropout mask vector; and the prediction vector (probability for each class) from the output layer.

In [ ]:
def forward_pass(x, W, dropout_rate=0.2):
    
    
    out_vals = {}
    
    h_vecs = []
    a_vecs = []
    dropout_vecs = []

    
   
    
    return out_vals
    

The `backward_pass` function computes the gradients and updates the weights for each matrix in the network from the output to the input. It takes as input 

- `x`: a list of vocabulary indices each corresponding to a word in the document (input)
- `y`: the true label
- `W`: a list of weight matrices connecting each part of the network, e.g. for a network with a hidden and an output layer: W[0] is the weight matrix that connects the input to the first hidden layer, W[1] is the weight matrix that connects the hidden layer to the output layer.
- `out_vals`: a dictionary of output values from a forward pass.
- `learning_rate`: the learning rate for updating the weights.
- `freeze_emb`: boolean value indicating whether the embedding weights will be updated.

and returns:

- `W`: the updated weights of the network.

Hint: the gradients on the output layer are similar to the multiclass logistic regression.

In [ ]:
def backward_pass(x, y, W, out_vals, lr=0.001, freeze_emb=False):
    
    
    return W




Finally you need to modify SGD to support back-propagation by using the `forward_pass` and `backward_pass` functions.

The `SGD` function takes as input:

- `X_tr`: array of training data (vectors)
- `Y_tr`: labels of `X_tr`
- `W`: the weights of the network (dictionary)
- `X_dev`: array of development (i.e. validation) data (vectors)
- `Y_dev`: labels of `X_dev`
- `lr`: learning rate
- `dropout`: regularisation strength
- `epochs`: number of full passes over the training data
- `tolerance`: stop training if the difference between the current and previous validation loss is smaller than a threshold
- `freeze_emb`: boolean value indicating whether the embedding weights will be updated (to be used by the backward pass function).
- `print_progress`: flag for printing the training progress (train/validation loss)


and returns:

- `weights`: the weights learned
- `training_loss_history`: an array with the average losses of the whole training set after each epoch
- `validation_loss_history`: an array with the average losses of the whole development set after each epoch

In [ ]:
def SGD(X_tr, Y_tr, W, X_dev=[], Y_dev=[], lr=0.001, 
        dropout=0.2, epochs=5, tolerance=0.001, freeze_emb=False, 
        print_progress=True):
    

    
    
    return W, training_loss_history, validation_loss_history

Now you are ready to train and evaluate your neural net. First, you need to define your network using the `network_weights` function followed by SGD with backprop:

In [ ]:
W = network_weights(vocab_size=len(vocab),embedding_dim=300,
                    hidden_dim=[], num_classes=3)

for i in range(len(W)):
    print('Shape W'+str(i), W[i].shape)

W, loss_tr, dev_loss = SGD(X_tr, Y_tr,
                            W,
                            X_dev=X_dev, 
                            Y_dev=Y_dev,
                            lr=0.001, 
                            dropout=0.2,
                            freeze_emb=False,
                            tolerance=0.01,
                            epochs=100)


NameError: name 'vocab' is not defined

Plot the learning process:

Compute accuracy, precision, recall and F1-Score:

In [ ]:
preds_te = [np.argmax(forward_pass(x, W, dropout_rate=0.0)['y']) 
            for x,y in zip(X_te,Y_te)]

print('Accuracy:', accuracy_score(Y_te,preds_te))
print('Precision:', precision_score(Y_te,preds_te,average='macro'))
print('Recall:', recall_score(Y_te,preds_te,average='macro'))
print('F1-Score:', f1_score(Y_te,preds_te,average='macro'))

### Discuss how did you choose model hyperparameters ? 

# Use Pre-trained Embeddings

Now re-train the network using GloVe pre-trained embeddings. You need to modify the `backward_pass` function above to stop computing gradients and updating weights of the embedding matrix.

Use the function below to obtain the embedding martix for your vocabulary. Generally, that should work without any problem. If you get errors, you can modify it.

In [ ]:
def get_glove_embeddings(f_zip, f_txt, word2id, emb_size=300):
    
    w_emb = np.zeros((len(word2id), emb_size))
    
    with zipfile.ZipFile(f_zip) as z:
        with z.open(f_txt) as f:
            for line in f:
                line = line.decode('utf-8')
                word = line.split()[0]
                     
                if word in vocab:
                    emb = np.array(line.strip('\n').split()[1:]).astype(np.float32)
                    w_emb[word2id[word]] +=emb
    return w_emb

In [ ]:
w_glove = get_glove_embeddings("glove.840B.300d.zip","glove.840B.300d.txt",word2id)

First, initialise the weights of your network using the `network_weights` function. Second, replace the weigths of the embedding matrix with `w_glove`. Finally, train the network by freezing the embedding weights: 

In [ ]:
preds_te = [np.argmax(forward_pass(x, W, dropout_rate=0.0)['y']) 
            for x,y in zip(X_te,Y_te)]

print('Accuracy:', accuracy_score(Y_te,preds_te))
print('Precision:', precision_score(Y_te,preds_te,average='macro'))
print('Recall:', recall_score(Y_te,preds_te,average='macro'))
print('F1-Score:', f1_score(Y_te,preds_te,average='macro'))

### Discuss how did you choose model hyperparameters ? 

# Extend to support deeper architectures 

Extend the network to support back-propagation for more hidden layers. You need to modify the `backward_pass` function above to compute gradients and update the weights between intermediate hidden layers. Finally, train and evaluate a network with a deeper architecture. Do deeper architectures increase performance?

In [ ]:
preds_te = [np.argmax(forward_pass(x, W, dropout_rate=0.0)['y']) 
            for x,y in zip(X_te,Y_te)]

print('Accuracy:', accuracy_score(Y_te,preds_te))
print('Precision:', precision_score(Y_te,preds_te,average='macro'))
print('Recall:', recall_score(Y_te,preds_te,average='macro'))
print('F1-Score:', f1_score(Y_te,preds_te,average='macro'))

### Discuss how did you choose model hyperparameters ? 

## Full Results

Add your final results here:

| Model | Precision  | Recall  | F1-Score  | Accuracy
|:-:|:-:|:-:|:-:|:-:|
| Average Embedding  |   |   |   |   |
| Average Embedding (Pre-trained)  |   |   |   |   |
| Average Embedding (Pre-trained) + X hidden layers    |   |   |   |   |


Please discuss why your best performing model is better than the rest and provide a bried error analaysis.